In [58]:
from ast import literal_eval
import ast
import numpy as np
import math
import re
import pandas as pd
import qgrid

import plotly.figure_factory as ff
import plotly.express as px
import plotly.graph_objects as go
from plotly.subplots import make_subplots
import matplotlib.pyplot as plt

from difflib import SequenceMatcher
from collections import Counter
import itertools

from fuzzywuzzy import fuzz
import nltk
from nltk.corpus import stopwords
from nltk.tokenize import word_tokenize
from nltk.stem.snowball import SnowballStemmer
from nltk.stem import PorterStemmer, WordNetLemmatizer

pd.set_option('display.max_columns', 1000)

In [59]:
#jaro functions
def sort_token_alphabetically(word):
    token = re.split('[,. ]', word)
    sorted_token = sorted(token)
    return ' '.join(sorted_token)

def get_jaro_distance(first, second, winkler=True, winkler_ajustment=True,
                      scaling=0.1, sort_tokens=True):
    """
    :param first: word to calculate distance for
    :param second: word to calculate distance with
    :param winkler: same as winkler_ajustment
    :param winkler_ajustment: add an adjustment factor to the Jaro of the distance
    :param scaling: scaling factor for the Winkler adjustment
    :return: Jaro distance adjusted (or not)
    """
    if sort_tokens:
        first = sort_token_alphabetically(first)
        second = sort_token_alphabetically(second)

    if not first or not second:
        raise JaroDistanceException(
            "Cannot calculate distance from NoneType ({0}, {1})".format(
                first.__class__.__name__,
                second.__class__.__name__))

    jaro = _score(first, second)
    cl = min(len(_get_prefix(first, second)), 4)

    if all([winkler, winkler_ajustment]):  # 0.1 as scaling factor
        return round((jaro + (scaling * cl * (1.0 - jaro))) * 100.0) / 100.0

    return jaro

def _score(first, second):
    shorter, longer = first.lower(), second.lower()

    if len(first) > len(second):
        longer, shorter = shorter, longer

    m1 = _get_matching_characters(shorter, longer)
    m2 = _get_matching_characters(longer, shorter)

    if len(m1) == 0 or len(m2) == 0:
        return 0.0

    return (float(len(m1)) / len(shorter) +
            float(len(m2)) / len(longer) +
            float(len(m1) - _transpositions(m1, m2)) / len(m1)) / 3.0

def _get_diff_index(first, second):
    if first == second:
        pass

    if not first or not second:
        return 0

    max_len = min(len(first), len(second))
    for i in range(0, max_len):
        if not first[i] == second[i]:
            return i

    return max_len

def _get_prefix(first, second):
    if not first or not second:
        return ""

    index = _get_diff_index(first, second)
    if index == -1:
        return first

    elif index == 0:
        return ""

    else:
        return first[0:index]

def _get_matching_characters(first, second):
    common = []
    limit = math.floor(min(len(first), len(second)) / 2)

    for i, l in enumerate(first):
        left, right = int(max(0, i - limit)), int(
            min(i + limit + 1, len(second)))
        if l in second[left:right]:
            common.append(l)
            second = second[0:second.index(l)] + '*' + second[
                                                       second.index(l) + 1:]

    return ''.join(common)

def _transpositions(first, second):
    return math.floor(
        len([(f, s) for f, s in zip(first, second) if not f == s]) / 2.0)

def get_top_matches(reference, value_list, max_results=None):
    scores = []
    if not max_results:
        max_results = len(value_list)
    for val in value_list:
#     for val in value_list.split():
        score_sorted = get_jaro_distance(reference, val)
        score_unsorted = get_jaro_distance(reference, val, sort_tokens=False)
        scores.append((val, max(score_sorted, score_unsorted)))
    scores.sort(key=lambda x: x[1], reverse=True)

    return scores[:max_results]

class JaroDistanceException(Exception):
    def __init__(self, message):
        super(Exception, self).__init__(message)

In [60]:
#load data
df = pd.read_csv('org_norm_final.csv')

#create interactive table
qgrid_df = qgrid.show_grid(df, show_toolbar=True)
print(df.shape)
qgrid_df

(10000, 2)


QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

In [61]:
#jaro test run
df = pd.read_csv('org_norm_final.csv')
df['parent_org_name']=df['parent_org_name'].str.replace(',','')

#remove special characters
spec_chars = ["!",'"',"#","%","&","'","(",")",
              "*","+","-",".","/",":",";","<",
              "=",">","?","@","[","\\","]","^","_",
              "`","{","|","}","~","–"]

for char in spec_chars:
    df['parent_org_name'] = df['parent_org_name'].str.replace(char, '')
    
spec_chars1 = ["!","#","%","&","'","(",")",
              "*","+","-",".","/",":",";","<",
              "=",">","?","@","\\","^","_",
              "`","{","|","}","~","–"]

for char in spec_chars1:
    df['children_org_name_list'] = df['children_org_name_list'].str.replace(char, '')

#remove stop words
stop = stopwords.words('english')
df['parent_org_name'] = df['parent_org_name'].apply(lambda x: ' '.join([word for word in x.split() if word not in (stop)]))
df['children_org_name_list'] = df['children_org_name_list'].apply(lambda x: ' '.join([word for word in x.split() if word not in (stop)]))

#apply stemming
porter_stemmer = PorterStemmer()
def stem_sentences(sentence):
    tokens = sentence.split()
    stemmed_tokens = [porter_stemmer.stem(token) for token in tokens]
    return ' '.join(stemmed_tokens)

df['parent_org_name'] = df['parent_org_name'].apply(stem_sentences)
df['children_org_name_list'] = df['children_org_name_list'].apply(stem_sentences)

df.head(5)

parent_org_name                             children_org_name_list
0           myllc  ["myalyk oleksandr nychyporovych pp","myliu sr...
1        ydea srl  ["yd confecco ltda","yda","yda insaat sanayi v...
2          hyonix  ["hymax talk solutions","hynix semiconductor i...
3   mjn enterpris  ["mjm interant inc","mjn enterprises","shanti ...
4  ltd yuriapharm         ["ltd yuriapharm","yuriypra law offic pc"]

In [62]:
#convert to strings, apply and sort jaro function
df['children_org_name_list'] = df.children_org_name_list.apply(literal_eval)
df['jaro_func_results'] = df.agg(lambda x: get_top_matches(*x), axis=1)
df['jaro_func_results'] = df['jaro_func_results'].apply(sorted)

#create ge cols
df['bt_80_89'] = df.jaro_func_results.apply(lambda x: [val for val in x if val[1] >= 0.8 and val[1] <= 0.89])
df['ge_75'] = df.jaro_func_results.apply(lambda x: [val for val in x if val[1] >= 0.75])
df['bt_70_79'] = df.jaro_func_results.apply(lambda x: [val for val in x if val[1] >= 0.7 and val[1] <= 0.79])
df['bt_60_69'] = df.jaro_func_results.apply(lambda x: [val for val in x if val[1] >= 0.6 and val[1] <= 0.69])
df['ge_50'] = df.jaro_func_results.apply(lambda x: [val for val in x if val[1] >= 0.50])
df['ge_25'] = df.jaro_func_results.apply(lambda x: [val for val in x if val[1] >= 0.25])

df.head(5)

parent_org_name                             children_org_name_list  \
0           myllc  [myalyk oleksandr nychyporovych pp, myliu srl,...   
1        ydea srl  [yd confecco ltda, yda, yda insaat sanayi veti...   
2          hyonix  [hymax talk solutions, hynix semiconductor inc...   
3   mjn enterpris  [mjm interant inc, mjn enterprises, shanti tow...   
4  ltd yuriapharm            [ltd yuriapharm, yuriypra law offic pc]   

                                   jaro_func_results       bt_80_89  \
0  [(myalyk oleksandr nychyporovych pp, 0.65), (m...             []   
1  [(yd confecco ltda, 0.62), (yda, 0.83), (yda i...  [(yda, 0.83)]   
2  [(hymax talk solutions, 0.64), (hynix semicond...             []   
3  [(mjm interant inc, 0.71), (mjn enterprises, 0...             []   
4  [(ltd yuriapharm, 1.0), (yuriypra law offic pc...             []   

                                               ge_75  \
0  [(myliu srl, 0.75), (myllc, 1.0), (myloc manag...   
1  [(yda, 0.83), (ydea, 0.9), (ydea srl, 1.0), (y...   
2  [(hynix semiconductor inc, 0.75), (hyonix, 1.0...   
3                          [(mjn enterprises, 0.97)]   
4                            [(ltd yuriapharm, 1.0)]   

                                            bt_70_79  \
0     [(myliu srl, 0.75), (myloc manag IT ag, 0.77)]   
1                                      [(ydh, 0.71)]   
2  [(hynix semiconductor inc, 0.75), (intercan hy...   
3                         [(mjm interant inc, 0.71)]   
4                                                 []   

                                            bt_60_69  \
0        [(myalyk oleksandr nychyporovych pp, 0.65)]   
1  [(yd confecco ltda, 0.62), (yda insaat sanayi ...   
2                     [(hymax talk solutions, 0.64)]   
3                [(shanti town mjini clients, 0.61)]   
4                                                 []   

                                               ge_50  \
0  [(myalyk oleksandr nychyporovych pp, 0.65), (m...   
1  [(yd confecco ltda, 0.62), (yda, 0.83), (yda i...   
2  [(hymax talk solutions, 0.64), (hynix semicond...   
3  [(mjm interant inc, 0.71), (mjn enterprises, 0...   
4  [(ltd yuriapharm, 1.0), (yuriypra law offic pc...   

                                               ge_25  
0  [(myalyk oleksandr nychyporovych pp, 0.65), (m...  
1  [(yd confecco ltda, 0.62), (yda, 0.83), (yda i...  
2  [(hymax talk solutions, 0.64), (hynix semicond...  
3  [(mjm interant inc, 0.71), (mjn enterprises, 0...  
4  [(ltd yuriapharm, 1.0), (yuriypra law offic pc...

In [63]:
#create just jaro scores col
df['jaro_func_score'] = df.jaro_func_results.apply(lambda x: [val[1] for val in x])

#function to add a bunch of character comparison columns
#names of columns listed in resultsx.append lines
def total_chars(row):
    
    results0 = []
    results1 = []
    results2 = []
    results3 = []
    results4 = []
    results5 = []
    results6 = []
    results7 = []
    
    p = row['parent_org_name'].lower()
    for i in row['children_org_name_list']:
        
        t = i.lower()
        
        dict1 = Counter(p)
        dict2 = Counter(t)
        
        commonDict = dict1 & dict2
        
        if len(commonDict) == 0:
            print -1
            return
    
        commonDict = list(set(dict1 & dict2)) #commonChars
        commonChars = list(set(dict1 + dict2)) #totalUniqueChars
        allChars = len(dict1) + len(dict2) #countallchars
        
        results0.append((i, len(commonDict))[1]) #countCommonChars
        results1.append((i, len(commonChars))) #totalUniqueChars
        results2.append((i, allChars)[1]) #countTotalUniqueChars
        results3.append((i, sum(int(k==v) for k,v in zip(t, p)))) #samePosition
        results4.append((i, sum(int(k==v) for k,v in zip(t, p)))[1]) #countSamePosition
        results5.append((i, SequenceMatcher(None, t, p).find_longest_match(0, len(t), 0, len(p))[2])) #consecutiveMatchingChars
        results6.append((i, round(SequenceMatcher(None, t, p).ratio(),2))) #consecutiveCharsRatio #slightly off?
        results7.append((i, round(SequenceMatcher(None, t, p).ratio(),2))[1]) #sequence_matcher_ratio

    return pd.Series([results0, results1, results2, results3, results4, results5, results6, results7])

df[['count_common_chars'
    , 'total_unique_chars'
    , 'count_total_unique_chars'
    , 'same_location'
    , 'count_same_position'
    , 'consecutive_chars'
    , 'consecutive_chars_ratio'
    , 'sequence_matcher_ratio'
   ]]  = df.apply(total_chars, axis=1)

#create percent matched columns
df['percentMatched'] = df.apply(lambda x: [np.round(x['count_common_chars'][i]/x['count_total_unique_chars'][i], 2) 
                                           for i in range(len(x['count_common_chars']))], axis = 1)
df['percentSamePosition'] = df.apply(lambda x: [np.round(x['count_same_position'][i]/x['count_total_unique_chars'][i], 2) 
                                                for i in range(len(x['count_common_chars']))], axis = 1)

#create and order jaro and sequencer diff column
df['jaro_sequencer_diff'] = df.apply(lambda x: [np.round(
    x['jaro_func_score'][i] - 
    x['sequence_matcher_ratio'][i],2) for i in range(len(x['jaro_func_score']))
], axis = 1)

df['jaro_sequencer_diff_sorted'] = [sorted(l) for l in df['jaro_sequencer_diff']]

#create and sort min/max cols of jaro/sequencer
df['jaro_min'] = df.jaro_func_score.apply(min)
df['jaro_max'] = df.jaro_func_score.apply(max)
df['sequence_min'] = df.sequence_matcher_ratio.apply(min)
df['sequence_max'] = df.sequence_matcher_ratio.apply(max)
df['jaro_sequencer_diff_max'] = df.jaro_sequencer_diff_sorted.apply(max)
df['jaro_sequencer_diff_min'] = df.jaro_sequencer_diff_sorted.apply(min)

#split parent column into list of tokens/words and create column
parent_org_name_list = []
for i in df.parent_org_name:
    x = i.split()
    parent_org_name_list.append(x)

df['parent_org_name_list'] = parent_org_name_list

#split child column into sublists with each word as an element
df['children_org_name_sublists'] = df.children_org_name_list.apply(lambda l: [s.split() for s in l])

#create full df
df = df[['parent_org_name', 'parent_org_name_list', 'children_org_name_list', 'children_org_name_sublists', 'jaro_func_results',
       'ge_25', 'ge_50', 'ge_75', 'bt_60_69', 'bt_70_79', 'bt_80_89', 
       'jaro_func_score', 'jaro_min', 'jaro_max',
       'sequence_matcher_ratio', 'sequence_min', 'sequence_max',
       'jaro_sequencer_diff', 'jaro_sequencer_diff_sorted',
       'jaro_sequencer_diff_min', 'jaro_sequencer_diff_max',
       'count_common_chars', 'count_total_unique_chars', 'count_same_position',
       'percentMatched', 'percentSamePosition',
       'total_unique_chars', 'same_location', 'consecutive_chars', 'consecutive_chars_ratio'
        ]]

#create interactive table
qgrid_df1 = qgrid.show_grid(df, show_toolbar=True)
qgrid_df1

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

In [65]:
#filter df cols
df1 = df[['parent_org_name'
          ,'parent_org_name_list'
          ,'children_org_name_list'
          ,'children_org_name_sublists'
          ,'jaro_func_score'
          ,'sequence_matcher_ratio']]

#run jaro function on each word
def jaro_word_scores(x, y):
    return [[(get_top_matches(u, [v])[0][1]) for v in w] for u in x for w in y] 

#get jaro scores for each word
df1['jaro_word_scores'] = df1.apply(lambda row: jaro_word_scores(row['parent_org_name_list'], row['children_org_name_sublists']), axis = 1)

#create avg jaro score per company word column
df1['avg_jaro_word_scores'] = df1.jaro_word_scores.apply(lambda x : [[np.mean(y)] for y in x ])

#filter df cols
df1.columns = ['parent_org_name'
               ,'parent_org_name_list'
               ,'children_org_name_list'
               ,'children_org_name_sublists'
               ,'jaro_company_name_scores'
               ,'sequence_company_name_scores'
               ,'jaro_company_word_scores'
               ,'avg_jaro_company_word_scores']

#create filters for avg jaro company scores
df1['ge_05'] = df1['avg_jaro_company_word_scores'].apply(lambda x: max(e[0] for e in x) >= 0.5)
df1['ge_75'] = df1['avg_jaro_company_word_scores'].apply(lambda x: max(e[0] for e in x) >= 0.75)
df1['ge_85'] = df1['avg_jaro_company_word_scores'].apply(lambda x: max(e[0] for e in x) >= 0.85)

#value counts per jaro company word score bins
print('ge .5:', df1['ge_05'].value_counts())
print('')
print('ge .75:', df1['ge_75'].value_counts())
print('')
print('ge .85:', df1['ge_85'].value_counts())

#print interactive table
print(df1.shape)
qgrid_df1 = qgrid.show_grid(df1, show_toolbar=True)
qgrid_df1

ge .5: True     9830
False     170
Name: ge_05, dtype: int64

ge .75: True     6642
False    3358
Name: ge_75, dtype: int64

ge .85: True     5261
False    4739
Name: ge_85, dtype: int64
(10000, 11)


QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

In [66]:
#filtered df with avg jaro company word sacores >= .85
df2 = df1[df1['ge_85'] == True][['parent_org_name'
                           ,'children_org_name_list'
                           ,'avg_jaro_company_word_scores']]

#create column with the element with the best avg. jaro word score
df2['best_child_match'] = [
    [value for value, score in zip(c1, c2) if score[0] >= .85 if score[0] < 1.0]
    for c1, c2 in zip(df2['children_org_name_list'], df2['avg_jaro_company_word_scores'])
]

#create column with the best avg. jaro word score
df2['best_child_jaro_score'] = [
    [score[0] for score in c2 if score[0] >= .85 if score[0] < 1.0]
    for c2 in df2['avg_jaro_company_word_scores']]

#filter out rows with null lists
df2 = df2[df2.astype(str)['best_child_match'] != '[]'][['parent_org_name','best_child_match','best_child_jaro_score']]

#create col of jaro scores not in list
df2['jaro_score_list'] = [','.join(map(str, l)) for l in df2['best_child_jaro_score']]

#create column of frequency of jaro scores
df2['freq'] = df2.groupby('jaro_score_list')['jaro_score_list'].transform('count')

#filter out columns
df2 = df2[['parent_org_name','best_child_match','jaro_score_list','freq']]

#print interactive table
qgrid_df2 = qgrid.show_grid(df2, show_toolbar=True)
qgrid_df2

QgridWidget(grid_options={'fullWidthRows': True, 'syncColumnCellResize': True, 'forceFitColumns': True, 'defau…

# Visualize the data

In [67]:
#create dataframe with all data
#filtered df with avg jaro company word sacores >= .85
df4 = df1[['parent_org_name','children_org_name_list','avg_jaro_company_word_scores']]

#create column with the element with the best avg. jaro word score
df4['best_child_match'] = [
    [value for value, score in zip(c1, c2) if score[0] >= .01 if score[0] <= 1.0]
    for c1, c2 in zip(df4['children_org_name_list'], df4['avg_jaro_company_word_scores'])
]

#create column with the best avg. jaro word score
df4['best_child_jaro_score'] = [
    [score[0] for score in c2 if score[0] >= .01 if score[0] <= 1.0]
    for c2 in df4['avg_jaro_company_word_scores']]

#filter out rows with null lists
df4 = df4[df4.astype(str)['best_child_match'] != '[]'][['parent_org_name','best_child_match','best_child_jaro_score']]

#print interactive table
qgrid_df4 = qgrid.show_grid(df4, show_toolbar=True)
# qgrid_df4

#flatten list of all jaro scores
best_child_jaro_score = list(df4.best_child_jaro_score)
df4_flat_list = [item for sublist in best_child_jaro_score for item in sublist]
df4 = pd.DataFrame()
df4['df4_flat_list'] = df4_flat_list
df4['freq'] = df4.groupby('df4_flat_list')['df4_flat_list'].transform('count')

df4.sort_values(by='df4_flat_list', ascending=False)

df4_flat_list  freq
16400       1.000000  3514
4441        1.000000  3514
25531       1.000000  3514
25526       1.000000  3514
25524       1.000000  3514
...              ...   ...
28593       0.043636     2
65523       0.043636     2
15317       0.043000     1
33266       0.042727     1
80151       0.042500     1

[96927 rows x 2 columns]

In [68]:
#jaro bin breakdown function
def jaro_bins(row):
    if row['df4_flat_list'] == 1.0:
        return 1.0
    elif row['df4_flat_list'] >= .9 < 1.0:
        return .9
    elif row['df4_flat_list'] >= .8 < .9:
        return .8
    elif row['df4_flat_list'] >= .7 < .8:
        return .7
    elif row['df4_flat_list'] >= .6 < .7:
        return .6
    elif row['df4_flat_list'] >= .5 < .6:
        return .5
    elif row['df4_flat_list'] >= .4 < .5:
        return .4
    elif row['df4_flat_list'] >= .3 < .4:
        return .3
    elif row['df4_flat_list'] >= .2 < .3:
        return .2
    elif row['df4_flat_list'] >= .1 < .2:
        return .1
    else:
        return 0

df4['jaro_score_bins'] = df4.apply(jaro_bins, axis=1)
df4

df4_flat_list  freq  jaro_score_bins
0           0.430000   528              0.4
1           0.660000   454              0.6
2           1.000000  3514              1.0
3           0.357500    28              0.3
4           0.666667   125              0.6
...              ...   ...              ...
96922       0.870000   268              0.8
96923       0.500000  4639              0.5
96924       0.196000    51              0.1
96925       0.357500    82              0.3
96926       0.500000  4639              0.5

[96927 rows x 3 columns]

In [69]:
#create pie_df
pie_df = pd.DataFrame(df4.jaro_score_bins.value_counts()).reset_index()
pie_df['percent'] = pie_df.jaro_score_bins / pie_df.jaro_score_bins.sum()

pie_df = pie_df.sort_values(by='index',ascending=False)
print(pie_df)

labels = list(pie_df['index'])
values = list(pie_df.percent)
# print(labels)
# print(values)

# pull is given as a fraction of the pie radius
fig = go.Figure(data=[go.Pie(labels=labels
                             ,values=values
                             ,textinfo='label+percent'
                             ,insidetextorientation='radial'
                             ,hole=.3
                             ,pull=[0,0.2, 0]
                     )])
fig.update_layout(
    title_text="<b>Jaro Score Bin Breakdown</b>"
    ,template = 'ggplot2'
)

fig.show()

    index  jaro_score_bins   percent
7     1.0             3514  0.036254
9     0.9             2366  0.024410
8     0.8             2643  0.027268
6     0.7             6912  0.071311
4     0.6             8985  0.092699
2     0.5            15875  0.163783
1     0.4            17932  0.185005
0     0.3            17948  0.185170
3     0.2            12627  0.130273
5     0.1             7240  0.074695
10    0.0              885  0.009131


In [70]:
#create x and y lists
x = list(df4['df4_flat_list'])
y = list(df4['freq'])

# Build figure
fig = go.Figure()

# Add first scatter trace with medium sized markers
fig.add_trace(
    go.Scatter(
        mode='markers',
        x=x,
        y=y,
        opacity=1.0,
        marker=dict(
            color='LightSkyBlue',
            size=16,
            line=dict(
                color='MediumPurple',
                width=2
            )
        ),
        name='Opacity 0.5'
    )
)

fig.update_layout(legend=dict(
    orientation="h"
    ,yanchor="bottom"
    ,y=1.02
    ,xanchor="right"
    ,x=1)
    ,title="<b>Distribution of Average Parent to Child Token Jaro Scores</b>"
    ,xaxis_title="Jaro Score"
    ,yaxis_title="Frequency"
    ,legend_title="Legend Title"
    ,width=1300
    ,height=700
    ,font=dict(
        size=14
        ,color="RebeccaPurple"
    )
)

fig.show()